Resources

---



https://huggingface.co/transformers/v4.3.3/_modules/transformers/training_args.html#:~:text=[docs]%20@dataclass%20class%20TrainingArguments:%20%22%22%22%20TrainingArguments%20is%20the%20subset%20of

https://github.com/NielsRogge/Transformers-Tutorials/blob/master/Table%20Transformer/Using_Table_Transformer_for_table_detection_and_table_structure_recognition.ipynb

https://pytorch.org/tutorials/beginner/blitz/tensor_tutorial.html?highlight=cuda#cuda-tensors

https://github.com/microsoft/table-transformer/blob/main/docs/INFERENCE.md

https://camelot-py.readthedocs.io/en/master/

https://github.com/tesseract-ocr/tesseract

https://www.kaggle.com/datasets/sreesankar711/pubtables-subset-100k

https://github.com/microsoft/table-transformer

In [ ]:
# Install packages
!pip install camelot-py[cv] ghostscript PyPDF2==1.26.0 pdf2image transformers matplotlib numpy opencv-python pandas torch tensorflow table-transformer transformers datasets
!apt-get install -y ghostscript
!pip install --upgrade camelot-py[cv]
!pip install pytesseract
!apt-get install -y tesseract-ocr
!apt-get install -y poppler-utils
#!pip install --upgrade pillow datasets
!pip install timm
!kaggle datasets download -d sreesankar711/pubtables-subset-100k
!unzip pubtables-subset-100k.zip -d /content/pubtables



     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.6/77.6 kB 4.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
INFO: pip is looking at multiple versions of camelot-py[cv] to determine which version is compatible with other requirements. This could take a while.
INFO: pip is looking at multiple versions of table-transformer to determine which version is compatible with other requirements. This could take a while.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.4/60.4 kB 2.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.0/57.0 kB 3.9 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of datasets to determine which version is compatible with other requirements. This could take a while.
INFO: pip is looking at multiple versions of multiprocess to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 582.4/582.4 kB 13.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

Streaming output truncated to the last 5000 lines.
  inflating: /content/pubtables/subset/words_val/PMC3004804_table_2_words.json  
  inflating: /content/pubtables/subset/words_val/PMC3004804_table_3_words.json  
  inflating: /content/pubtables/subset/words_val/PMC3004804_table_4_words.json  
  inflating: /content/pubtables/subset/words_val/PMC3004804_table_5_words.json  
  inflating: /content/pubtables/subset/words_val/PMC3004804_table_6_words.json  
  inflating: /content/pubtables/subset/words_val/PMC3004804_table_7_words.json  
  inflating: /content/pubtables/subset/words_val/PMC3004804_table_8_words.json  
  inflating: /content/pubtables/subset/words_val/PMC3004821_table_0_words.json  
  inflating: /content/pubtables/subset/words_val/PMC3004821_table_1_words.json  
  inflating: /content/pubtables/subset/words_val/PMC3004833_table_0_words.json  
  inflating: /content/pubtables/subset/words_val/PMC3004833_table_1_words.json  
  inflating: /content/pubtables/subset/words_val/PMC300483

In [ ]:
# Import libraries
import os
import json
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

# PDF libaries
import camelot
import ghostscript
import PyPDF2 as pypdf
from pdf2image import convert_from_path

# Image processsing libaries
import pytesseract
import cv2
import PIL
from PIL import Image
from torchvision.datasets import ImageFolder
from torchvision import transforms
from PyPDF2 import PdfFileReader

# Pytorch libraries
import torch
from torch.utils.data import DataLoader
from torchvision import datasets, transforms

# Transformer and datasets
import transformers
from transformers import TableTransformerForObjectDetection, Trainer, TrainingArguments, pipeline
from transformers import AutoImageProcessor, TableTransformerForObjectDetection, TrainingArguments, Trainer
from transformers import DefaultDataCollator
from transformers import Trainer, TrainingArguments, default_data_collator
import datasets
from datasets import load_dataset
from datasets import Dataset, Features, ClassLabel, Value, Image as ImageType

# Google Collab
from google.colab import files




In [ ]:
# Upload PDF file
upload = files.upload()
pdf_file = list(upload.keys())[0]

Saving test1.pdf to test1.pdf


In [ ]:
def extract_pdf_table(pdf_file):
    # Initialise tables list to store extracted tables
    tables = []

    # Extract tables using Camelot (stream)
    try:
        tables = camelot.read_pdf(pdf_file, pages='all', flavor='stream')
    except Exception as e:
        print(f"Error extracting table with Camelot (stream): [{e}]")
        # Extract using Camelot (lattice)
        try:
            tables = camelot.read_pdf(pdf_file, pages='all', flavor='lattice')
        except Exception as e:
            print(f"Error extracting table with Camelot (lattice): [{e}]")

    # If tables were sucessfully extracted using Camelot, return them
    if tables:
        print(f"Extracted {len(tables)} tables using Camelot.")
        return [table.df.values.tolist() for table in tables]

    # If Camelot was unsucessful use OCR
    print("Using OCR for image-based table extraction.")

    # Convert PDF to image using pdf2image
    images = convert_from_path(pdf_file, poppler_path="/usr/bin", fmt='png')

    # Initialise list to store extracted text from images
    extract_text_table = []

    # Extract text from images using Tesseract
    for i, image in enumerate(images):
      image = image = image.convert('RGB')
      text = pytesseract.image_to_string(image)
      extract_text_table.append(text)
      print(f"Extracted text from image [{i + 1}/{len(images)}]")

    # Process extracted text into structured data
    extracted_data = []
    for text in extract_text_table:
        rows = text.split('\n')  # Split text into rows
        for row in rows:
            if row.strip():  # Ignore empty rows
                extracted_data.append(row.strip().split())  # Split into columns

    return extracted_data  # Return structured data

    #upload = files.upload()
    #pdf_file = list(upload.keys())[0]

# Example use of extract_pdf_table function
if __name__ == "__main__":
    data = extract_pdf_table(pdf_file)
    print(data)

Using OCR for image-based table extraction.
Extracted text from image [1/1]
[["5-Bromo-2'-deoxyuridine", '(BrdU)', 'labeling*', 'of', 'MCF10A', 'cells', 'grown', 'in', 'monoculture', '(control', 'group)', 'and', 'in', 'co-cultures', 'with', 'normal'], ['breast-associated', 'fibroblasts', '(NAF)', 'and', 'carcinoma-associated', 'fibroblasts', '(CAF)'], ['Culture:', 'BrdL-labeling', 'indices', 'of', 'BrdU-labeling', 'indices', 'of', 'Comparison', 'of', 'BrdUHabeling', 'indices', 'of', 'MCFIOA', 'cells', 'between'], ['MCFIOA', 'cells', '(mean', '+', 'MCF10A', 'cells', 'mean', '+', 'groups', '(linear', 'regression}'], ['standard', 'error', 'af', 'the', 'mean)', 'standard', 'error', 'of', 'the', 'mean}'], ['MCF10A', '(n=', '6)', '30.343.0', '303230', 'MCFIOA', 'vs', 'MCFIOA', '+', 'NAF', '(P', '=', 'MCF1I0A', '+', 'NAF', 'vs', 'MCFIOA', '+'], ['=', '0.009)', 'CAF', '(P=', '0.501)'], ['NAF-1', '+', 'MCFIOA', '{np', '=', '7)', '21.9242', '16.1', '$2.6', '(n=', '19}'], ['NAF-2', '+', 'MCFIOA',

In [ ]:
# Convert table to JSON
def json_table(table):
  # Check if table has DataFrame 'df' attribute
  if hasattr(table, 'df'):
    header = table.df.values.tolist() # Get df header
    rows = table.df.values.tolist() # Get df rows
    # Return list of dictionaries
    return [dict(zip(header, row)) for row in rows]
  else:
    # If table is a list or tuple
    if table and isinstance(table, (list, tuple)) and len(table) > 1:
      header = table[0] # First element is header
      rows = table[1:] # Remaining elements are rows
      # Return list of dictionaries
      return [dict(zip(header, row)) for row in rows]
    else:
      print("Invalid table format for JSON conversion.")
      return []


In [ ]:
# Extract table from PDF file and store as tables
tables = extract_pdf_table(pdf_file)

# Convert extracted table to JSON
json_tables = [json_table(table) for table in tables]
with open('tables.json', 'w') as f:
  json.dump(json_tables, f)

Using OCR for image-based table extraction.
Extracted text from image [1/1]


In [ ]:
# Convert extracted table to an image
for i, table in enumerate(tables):
  df = pd.DataFrame(table)

  # Create new figure and axis for plotting
  fig, ax = plt.subplots()
  ax.axis('off')

  # Create table plot with DataFrame values and column labels
  plot_table = ax.table(cellText=df.values, colLabels=df.columns, loc='center')

  # Save plot as PNG image
  plt.savefig(f'table_{i}.png', bbox_inches='tight', pad_inches=0)
  plt.close()

In [ ]:
# Load pre-trained Table Transformer model
model = TableTransformerForObjectDetection.from_pretrained('microsoft/table-transformer-detection')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.23k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/115M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/46.8M [00:00<?, ?B/s]

Some weights of the model checkpoint at microsoft/table-transformer-detection were not used when initializing TableTransformerForObjectDetection: ['model.backbone.conv_encoder.model.layer2.0.downsample.1.num_batches_tracked', 'model.backbone.conv_encoder.model.layer3.0.downsample.1.num_batches_tracked', 'model.backbone.conv_encoder.model.layer4.0.downsample.1.num_batches_tracked']
- This IS expected if you are initializing TableTransformerForObjectDetection from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TableTransformerForObjectDetection from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [ ]:
# Load image processor
image_processor = AutoImageProcessor.from_pretrained("microsoft/table-transformer-detection")

preprocessor_config.json:   0%|          | 0.00/273 [00:00<?, ?B/s]

The `max_size` parameter is deprecated and will be removed in v4.26. Please specify in `size['longest_edge'] instead`.


In [ ]:
# Load training dataset
train_dataset = load_dataset('imagefolder', data_dir='/content/pubtables/subset/img_train')

# Load validation dataset
#val_dataset = load_dataset('imagefolder', data_dir='/content/pubtables/subset/img_val')



# Loads the annotations from the JSON files and associates them with their corresponding images, creating a dataset. Based on Feedback
"""
def load_dataset_with_labels(images_dir, annotations_dir, limit=100):
    dataset = {}

    for filename in os.listdir(annotations_dir):
        if filename.endswith('_words.json'):
            with open(os.path.join(annotations_dir, filename)) as f:
                annotations = json.load(f)

            image_name = filename.replace('_words.json', '.jpg')
            image_path = os.path.join(images_dir, image_name)

            if os.path.exists(image_path):
                if image_path not in dataset:
                    dataset[image_path] = []

                # Collect all annotations for this image
                for item in annotations:
                    labels = {
                        'text': item['text'],
                        'bbox': item['bbox']
                    }
                    dataset[image_path].append(labels)

                    # Debug output
                    print(f"Loaded: {image_path}, Text: {item['text']}")

                # Stop loading if we reach the limit of unique images
                if len(dataset) >= limit:
                    break
            else:
                print(f"Image not found: {image_path}")

    # Convert the dictionary to the desired format
    final_dataset = [{'image_path': img_path, 'labels': labels} for img_path, labels in dataset.items()]

    return final_dataset[:limit]  # Return only the first 100 images if more are collected

# Define directories
images_dir = '/content/pubtables/subset/img_train'
annotations_dir = '/content/pubtables/subset/words_train'

# Load the dataset with a limit of 100 unique images
train_dataset = load_dataset_with_labels(images_dir, annotations_dir, limit=100)

# Print the first 5 items to check
print(train_dataset[:5])
"""

Resolving data files:   0%|          | 0/60000 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

In [ ]:
# Test dataset
print(train_dataset['train'][0])


AttributeError: can't set attribute 'mode'

In [ ]:
# Subset of 100 examples from the training dataset
subset_training_dataset = train_dataset['train'].select(range(100))


In [ ]:
def preprocess_function(examples):
    # Define transformations
    transform = transforms.Compose([
        transforms.Resize((224, 224)), # Resize image
        transforms.ToTensor(),         # Convert image to Pytorch tensor
        transforms.Normalize(mean=[0.5, 0.5, 0.5], std=[0.5, 0.5, 0.5]) # Normalise pixel value
    ])

    # Find colum in dataset that contains image paths or image objects
    image_column = 'image_path'
    if image_column not in examples:
        image_column = 'image'  # Fallback to 'image' column
        if image_column not in examples:
            raise KeyError(f"Neither 'image_path' nor 'image' found in the dataset columns: {list(examples.keys())}")

    if 'pixel_values' in examples:
        return examples

    # Initialise 'pixel_values' as tensor list
    examples['pixel_values'] = []

    # Check image objects
    for image in examples[image_column]:
        try:
            # If PIL Image, convert to RGB
            pil_image = image.convert("RGB")
            # Apply transformations
            examples['pixel_values'].append(transform(pil_image))
        except (TypeError, ValueError, IOError, AttributeError) as e:
            print(f"Error processing image: {e}, type: {type(image)}")
            examples['pixel_values'].append(torch.zeros(3, 224, 224))  # Placeholder

    # Convert list of tensors to single tensor
    examples['pixel_values'] = torch.stack(examples['pixel_values'])

    return examples

In [ ]:
# Apply preprocessing function to the subset dataset
subset_training_dataset = subset_training_dataset.map(preprocess_function, batched=True)

# Apply preprocessing to the training dataset
#train_dataset = train_dataset.map(preprocess_function, batched=True)
# Apply preprocessing to the validation dataset
#val_dataset = val_dataset.map(preprocess_function, batched=True)




Map:   0%|          | 0/100 [00:00<?, ? examples/s]

AttributeError: can't set attribute 'mode'

In [ ]:
# Test preprocessing
print(subset_training_dataset[0])

{'image': <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=643x149 at 0x7AEFE0B87970>, 'pixel_values': [[[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.9607843160629272, 0.9450980424880981, 0.9372549057006836, 0.9529411792755127, 0.9764705896377563, 0.9529411792755127, 0.9372549057006836, 0.9529411792755127, 0.9529411792755127, 0.9529411792755127, 0.9686274528503418, 0.9921568632125854, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0

In [ ]:
# Prepare batch for training
def custom_data_collator(features):
    # Initialise dictionary to hold batch data
    batch = {}

    # Stack pixel value into tensor
    batch['pixel_values'] = torch.stack([f['pixel_values'] for f in features])

    # Handle labels
    if 'labels' in features[0]:
        batch['labels'] = [f['labels'] for f in features]

    return batch

In [ ]:
# Test dataset
print(subset_training_dataset[0])

{'image': <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=643x149 at 0x7AEFE0B85870>, 'pixel_values': [[[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.9607843160629272, 0.9450980424880981, 0.9372549057006836, 0.9529411792755127, 0.9764705896377563, 0.9529411792755127, 0.9372549057006836, 0.9529411792755127, 0.9529411792755127, 0.9529411792755127, 0.9686274528503418, 0.9921568632125854, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0

In [ ]:
# Test dataset
print(type(subset_training_dataset['pixel_values'][0]))

<class 'list'>


In [ ]:
# Training arguments
training_arguments = TrainingArguments(
    output_dir='./results',                    # Model prediction directory
    evaluation_strategy='epoch',               # Evaluation strategy during training
    save_strategy='epoch',                     # Save strategy during training
    save_total_limit=2,                        # Maximum number of checkpoints to save
    save_steps=100,                            # Save every 100 steps
    learning_rate=2e-5,                        # Learning rate
    per_device_train_batch_size=16,            # Training batch size
    per_device_eval_batch_size=16,             # Evaluation batch size
    num_train_epochs=3,                        # Training epochs
    logging_dir='./logs',                      # Logging directory
    logging_steps=10,                          # Log training
    remove_unused_columns=False,               # Do not remove unused columns in dataset
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
# Initialise Trainer for model training
trainer = Trainer(
    model=model,                               # Trained model
    args=training_arguments,                   # Training arguments
    train_dataset=train_dataset['train'],      # Training dataset
    data_collator=custom_data_collator         # Data collator for batch
    #eval_dataset=val_dataset['train'],        # Training validation data set
)

NameError: name 'Trainer' is not defined

In [ ]:
# Train model
trainer.train()

KeyError: 'pixel_values'

In [ ]:
# Test image on model
table_recogniser = pipeline('table-recognition', model=model)

# Load table image
test_image = Image.open('table_0.png')
table_recogniser(test_image)

# Convert prediction to JSON
predicted_tables = json.dumps(table_recogniser(test_image))
with open('predicted_tables.json', 'w') as f:
  f.write(predicted_tables)

print(prediction_json)

KeyError: "Unknown task table-recognition, available tasks are ['audio-classification', 'automatic-speech-recognition', 'depth-estimation', 'document-question-answering', 'feature-extraction', 'fill-mask', 'image-classification', 'image-feature-extraction', 'image-segmentation', 'image-to-image', 'image-to-text', 'mask-generation', 'ner', 'object-detection', 'question-answering', 'sentiment-analysis', 'summarization', 'table-question-answering', 'text-classification', 'text-generation', 'text-to-audio', 'text-to-speech', 'text2text-generation', 'token-classification', 'translation', 'video-classification', 'visual-question-answering', 'vqa', 'zero-shot-audio-classification', 'zero-shot-classification', 'zero-shot-image-classification', 'zero-shot-object-detection', 'translation_XX_to_YY']"